In [ ]:
!python -m pip install pyyaml==5.1
import sys, os, distutils.core
# Note: This is a faster way to install detectron2 in Colab, but it does not include all functionalities (e.g. compiled operators).
# See https://detectron2.readthedocs.io/tutorials/install.html for full installation instructions
!git clone 'https://github.com/facebookresearch/detectron2'
dist = distutils.core.run_setup("./detectron2/setup.py")
!python -m pip install {' '.join([f"'{x}'" for x in dist.install_requires])}
sys.path.insert(0, os.path.abspath('./detectron2'))


import torch, detectron2
!nvcc --version
TORCH_VERSION = ".".join(torch.__version__.split(".")[:2])
CUDA_VERSION = torch.__version__.split("+")[-1]
print("torch: ", TORCH_VERSION, "; cuda: ", CUDA_VERSION)


In [24]:
#install detectron2


# import some common libraries
import numpy as np
import os, json, cv2, random
#from google.colab.patches import cv2_imshow

# import some common detectron2 utilities
from detectron2 import model_zoo

from detectron2.engine import DefaultPredictor
from detectron2.config import get_cfg
from detectron2.utils.visualizer import Visualizer
from detectron2.data import MetadataCatalog, DatasetCatalog

In [25]:
# Some basic setup:
# Setup detectron2 logger
import detectron2
from detectron2.utils.logger import setup_logger
setup_logger()

# import some common libraries
import numpy as np
import os, json, cv2, random
#from google.colab.patches import cv2_imshow

# import some common detectron2 utilities
from detectron2 import model_zoo
from detectron2.engine import DefaultPredictor
from detectron2.config import get_cfg
from detectron2.utils.visualizer import Visualizer
from detectron2.data import MetadataCatalog, DatasetCatalog

In [26]:
DatasetCatalog.remove('bath1_sub_train')
MetadataCatalog.remove('bath1_sub_train')
DatasetCatalog.remove('bath1_sub_val')
MetadataCatalog.remove('bath1_sub_val')

In [27]:

from detectron2.structures import BoxMode
import json
import os
from detectron2.data import DatasetCatalog, MetadataCatalog
import numpy as np

classname=[]




def get_bathroom_dicts(img_dir):
    #dataset_dictsall = []
    dataset_dicts = []
    #I have two folders, one for training and one for validation
     #read files in the training folder and validation folder
    dir_neg=img_dir+'/negative'
    dir_pos=img_dir+'/positive'
    for d in [dir_pos, dir_neg]:
       
    #read the files in the dir_neg and dir_pos
    #print(dir_neg)
    #print(dir_pos)
    
    #print(current_path)
    #print(os.listdir(dir_neg)) 
    #print(os.listdir(dir_pos))
    #print(os.listdir(dir_neg and dir_pos))
        
    #
    
     for filename in os.listdir(d):
 
 
     #
    
      if filename.endswith('.json'):  # Check if the file is a JSON file
        file_path = os.path.join(d,filename)
        #print(file_path)
        with open(file_path, 'r') as file:
            data = json.load(file)

            
        

            
            for key, value in data.items():
        

         
        # For each image annotation in the JSON
               if "annotation" in key:
                record = {}
            #check value contains the string filename and return the index
          
                filename = os.path.join(d,value["filename"])
                #print(filename)
           
            
    
                height, width, _ = value["imsize"]
           

                record["file_name"] = filename
            
                record["height"] = height
                record["width"] = width
            

            # Annotation information
                objs = []
                for anno in value["object"]:
                 #print(anno)
                 if "polygon" in anno:
                    # Create a bounding box for each object
                    poly = anno["polygon"]
                    px = poly["x"]
                    py = poly["y"]
                    poly = [(x, y ) for x, y in zip(px, py)]
                    poly = [p for x in poly for p in x]
        
                    if anno["raw_name"] not in classname:
                        classname.append(anno["raw_name"])


                    value = {
                        "bbox": [np.min(px), np.min(py), np.max(px), np.max(py)],
                        "bbox_mode": BoxMode.XYXY_ABS,
                        "segmentation": [poly],
                        "category_id": classname.index(anno["raw_name"]),
                        
                        
                        #"iscrowd": 0,
                    }
                    #insert the class name into the list without repeating
                    
                    objs.append(value)
                    
                




            #print(objs)
            #print(classname)
                    

                record["annotations"] = objs
                
                dataset_dicts.append(record)
                
        #dataset_dictsall.append(dataset_dicts)
    print(len(classname))
        
    return dataset_dicts
    







            
#get_bathroom_dicts("/home/jiayi/ADE_bathroom/sub_train")
for d in ["sub_train", "sub_val"]:
    #getbathroom=get_bathroom_dicts("/home/jiayi/ADE_bathroom/" + d)
    
    DatasetCatalog.register("bath1_" + d, lambda d=d:get_bathroom_dicts("/home/jiayi/ADE_bathroom/" + d))

    
   
    
    #print("OK")
    MetadataCatalog.get("bath1_" + d).set(thing_classes=classname)
bath_metadata = MetadataCatalog.get("bath1_sub_train")
    #show the registered images

    #show the path for the   images
print(DatasetCatalog.get("bath1_sub_train"))




393
[{'file_name': '/home/jiayi/ADE_bathroom/sub_train/positive/ADE_train_00002646.jpg', 'height': 512, 'width': 384, 'annotations': [{'bbox': [23, 372, 313, 512], 'bbox_mode': <BoxMode.XYXY_ABS: 0>, 'segmentation': [[119, 372, 24, 430, 23, 511, 304, 512, 313, 418]], 'category_id': 0}, {'bbox': [60, 320, 108, 348], 'bbox_mode': <BoxMode.XYXY_ABS: 0>, 'segmentation': [[92, 320, 108, 326, 108, 338, 81, 348, 65, 347, 60, 339, 64, 329]], 'category_id': 1}, {'bbox': [92, 405, 159, 477], 'bbox_mode': <BoxMode.XYXY_ABS: 0>, 'segmentation': [[114, 405, 137, 407, 150, 412, 156, 422, 159, 438, 152, 447, 150, 455, 149, 476, 112, 477, 92, 424, 98, 417, 105, 411]], 'category_id': 2}, {'bbox': [71, 368, 101, 387], 'bbox_mode': <BoxMode.XYXY_ABS: 0>, 'segmentation': [[81, 368, 99, 376, 101, 385, 94, 387, 90, 382, 74, 383, 71, 380, 72, 373]], 'category_id': 1}, {'bbox': [2, 494, 77, 511], 'bbox_mode': <BoxMode.XYXY_ABS: 0>, 'segmentation': [[3, 495, 25, 494, 47, 497, 65, 500, 77, 508, 77, 511, 2, 510]

In [ ]:
dget= get_bathroom_dicts("/home/jiayi/ADE_bathroom/sub_train")
#only read the img file
import random
import cv2
from detectron2.utils.visualizer import Visualizer
from detectron2.data import MetadataCatalog
import matplotlib.pyplot as plt
#randomly select 2 images to sho
#only read the file with jpg format


for d in random.sample(dget, 2):
    print(dget)
    print(d["file_name"])
    
    img = cv2.imread(d["file_name"])
    #check the image path for cv2.imread.
    
    
    visualizer = Visualizer(img[:, :, ::-1], metadata=MetadataCatalog.get("bath1_sub_train"), scale=0.5)
    print(d)
    vis = visualizer.draw_dataset_dict(d)
    plt.imshow(vis.get_image()[:, :, ::-1])
    plt.axis('off')
    plt.show()
   
    
    

In [ ]:
from detectron2.engine import DefaultTrainer
from detectron2.config import get_cfg
from detectron2 import model_zoo
from detectron2.engine import DefaultPredictor
from detectron2.config import get_cfg
from detectron2.utils.visualizer import Visualizer

cfg = get_cfg()

cfg.merge_from_file(model_zoo.get_config_file("COCO-InstanceSegmentation/mask_rcnn_R_50_FPN_3x.yaml"))
cfg.DATASETS.TRAIN = ("bath1_sub_train",)
cfg.DATASETS.TEST = ()
cfg.DATALOADER.NUM_WORKERS = 2
cfg.MODEL.WEIGHTS = model_zoo.get_checkpoint_url("COCO-InstanceSegmentation/mask_rcnn_R_50_FPN_3x.yaml")  # Let training initialize from model zoo
cfg.SOLVER.IMS_PER_BATCH = 2  # This is the real "batch size" commonly known to deep learning people
cfg.SOLVER.BASE_LR = 0.01  # pick a good LR
cfg.SOLVER.MAX_ITER =200    # 300 iterations seems good enough for this toy dataset; you will need to train longer for a practical dataset
cfg.SOLVER.STEPS = []        # do not decay learning rate
cfg.MODEL.ROI_HEADS.BATCH_SIZE_PER_IMAGE = 128   # The "RoIHead batch size". 128 is faster, and good enough for this toy dataset (default: 512)
cfg.MODEL.ROI_HEADS.NUM_CLASSES = 393   # only has one class (ballon). (see https://detectron2.readthedocs.io/tutorials/datasets.html#update-the-config-for-new-datasets)
# NOTE: this config means the number of classes, but a few popular unofficial tutorials incorrect uses num_classes+1 here.

os.makedirs(cfg.OUTPUT_DIR, exist_ok=True)
cfg.MODEL.DEVICE='cpu'
trainer = DefaultTrainer(cfg) 
trainer.resume_or_load(resume=False)
trainer.train()

In [31]:
cfg.MODEL.WEIGHTS = os.path.join(cfg.OUTPUT_DIR, "model_final.pth")  # path to the model we just trained
cfg.MODEL.ROI_HEADS.SCORE_THRESH_TEST = 0.5   # set a custom testing threshold
predictor = DefaultPredictor(cfg)

[05/23 22:23:11 d2.checkpoint.detection_checkpoint]: [DetectionCheckpointer] Loading from ./output/model_final.pth ...
[Checkpointer] Loading from ./output/model_final.pth ...


In [ ]:
from detectron2.utils.visualizer import ColorMode
%pip install owlready2
%pip install rdflib
from rdflib import Graph, Literal, RDF, RDFS, OWL, Namespace, URIRef
from rdflib.namespace import XSD


#create one empty knowledge graph
# Create a Graph
g = Graph()
# Create a namespace object for the ontology namespace
#base for xml


rdf=Namespace("http://www.w3.org/1999/02/22-rdf-syntax-ns#")
xsd = Namespace("http://www.w3.org/2001/XMLSchema#")
xml=Namespace("http://www.w3.org/XML/1998/namespace")
owl=Namespace("http://www.w3.org/2002/07/owl#")
rdfs=Namespace("http://www.w3.org/2000/01/rdf-schema#")
bathroomspace=Namespace("http://example.org/ade20K_bathroom#")

#bind the namespace to the graph
g.bind("rdf", rdf)
g.bind("xsd", xsd)
g.bind("xml", xml)
g.bind("owl", owl)
g.bind("rdfs", rdfs)
g.bind("bathroom", bathroomspace)

#ontology metadata
ontology = URIRef(bathroomspace)
g.add((ontology, RDF.type, OWL.Ontology))
g.add((ontology, RDFS.comment, Literal("A simple ontology for a library system")))





dataset_dicts = get_bathroom_dicts("/home/jiayi/ADE_bathroom/sub_test")
for d in dataset_dicts:    
    im = cv2.imread(d["file_name"])
    #PRINT THE IMAGE PATH
    print(d["file_name"])

    outputs = predictor(im)  # format is documented at https://detectron2.readthedocs.io/tutorials/models.html#model-output-format
    v = Visualizer(im[:, :, ::-1],
                   metadata=bath_metadata, 
                   scale=0.5, 
                   instance_mode=ColorMode.IMAGE_BW   # remove the colors of unsegmented pixels. This option is only available for segmentation models
    )
    #v = Visualizer(im[:, :, ::-1], MetadataCatalog.get(cfg.DATASETS.TRAIN[0]), scale=1.2)
    out = v.draw_instance_predictions(outputs["instances"].to("cpu"))

    plt.axis('off')
    plt.imshow(out.get_image())
#print the instance segmentation 
    plt.show()


#store the class in one list from metadata and remove the unduplicated class name
    class_list=[]
    for i in range(len(outputs["instances"].pred_classes)):
     if MetadataCatalog.get(cfg.DATASETS.TRAIN[0]).thing_classes[outputs["instances"].pred_classes[i]] not in class_list:
      class_list.append(MetadataCatalog.get(cfg.DATASETS.TRAIN[0]).thing_classes[outputs["instances"].pred_classes[i]])
    print(len(class_list))


#

#add the class to the ontology
    for i in range(len(class_list)):
     class_name=URIRef(bathroomspace+class_list[i])
     g.add((class_name, RDF.type, OWL.Class))
    
#add the object property to the ontology
    g.add((bathroomspace.contains, RDF.type, OWL.ObjectProperty))
#g.add((bathroom.contains, RDFS.domain, bathroom))


#create the image as the individual for the ontology
    image=URIRef(d["file_name"])
    g.add((image, RDF.type, owl.NamedIndividual))
    

#add the class to the individual
    for i in range(len(class_list)):
     class_name=URIRef(bathroomspace+class_list[i])
     
     g.add((image, bathroomspace.contains, class_name))
g.serialize('/home/jiayi/ADE_bathroom/bathroom.owl', format='xml')







#show the graph to the owl file













   

In [33]:
#create one JSON file for the ontology
import json,os
# owl file path
data_path = "/home/jiayi/ADE_bathroom/bathroom.owl"
# json file path
json_path = "/home/jiayi/ADE_bathroom/bathroom.json"
os.chdir('/home/jiayi/ADE_bathroom')


#read the postive and negative images from  gthe owl file
postive_set=[]
negative_set=[]


#read the individual from the owl file
g = Graph()
g.parse(data_path, format='xml')
#iterate the owl file
for s, p, o in g:
    #print(s, p, o)
    if "positive" in str(s) and str(s) not in postive_set:
        postive_set.append(str(s))
    if "negative" in str(s)and str(s) not in negative_set:
        negative_set.append(str(s))
print(postive_set)  
print(negative_set)


#create the json structure for the ontology
data = {
    "data_path": data_path,
    "problems":{
            "lp_1": {
        
                "positive_examples": postive_set,
                "negative_examples": negative_set
            }
    }
}
#save the json file
with open(json_path, 'w') as json_file:
    json.dump(data, json_file, indent=4)
#show the json file


['file:///home/jiayi/ADE_bathroom/sub_test/positive/ADE_val_00000092.jpg', 'file:///home/jiayi/ADE_bathroom/sub_test/positive/ADE_val_00000094.jpg', 'file:///home/jiayi/ADE_bathroom/sub_test/positive/ADE_val_00000104.jpg', 'file:///home/jiayi/ADE_bathroom/sub_test/positive/ADE_val_00001084.jpg', 'file:///home/jiayi/ADE_bathroom/sub_test/positive/ADE_val_00000083.jpg', 'file:///home/jiayi/ADE_bathroom/sub_test/positive/ADE_val_00000099.jpg', 'file:///home/jiayi/ADE_bathroom/sub_test/positive/ADE_val_00001097.jpg', 'file:///home/jiayi/ADE_bathroom/sub_test/positive/ADE_val_00001107.jpg', 'file:///home/jiayi/ADE_bathroom/sub_test/positive/ADE_val_00000077.jpg', 'file:///home/jiayi/ADE_bathroom/sub_test/positive/ADE_val_00000079.jpg', 'file:///home/jiayi/ADE_bathroom/sub_test/positive/ADE_val_00001077.jpg', 'file:///home/jiayi/ADE_bathroom/sub_test/positive/ADE_val_00000103.jpg', 'file:///home/jiayi/ADE_bathroom/sub_test/positive/ADE_val_00000089.jpg', 'file:///home/jiayi/ADE_bathroom/sub_